# 特征工程技术

搬运参考：https://www.kaggle.com/c/ieee-fraud-detection/discussion/108575

### 关于编码
在执行编码时，最好训练和测试集一起编码，如下所示

In [ ]:
df = pd.concat([train[col],test[col]],axis=0)
# PERFORM FEATURE ENGINEERING HERE
train[col] = df[:len(train)]
test[col] = df[len(train):]

### NAN值加工
如果将np.nan给LGBM，那么在每个树节点分裂时，它会分裂非 NAN 值，然后将所有 NAN 发送到左节点或右节点，这取决于什么是最好的。

因此，NAN 在每个节点都得到特殊处理，并且可能会变得过拟合。

通过简单地将所有 NAN 转换为低于所有非 NAN 值的负数（例如 - 999），来防止测试集过拟合。

In [ ]:
df[col].fillna(-999, inplace=True)

这样LGBM将不再过度处理 NAN。相反，它会给予它与其他数字相同的关注。可以尝试两种方法，看看哪个给出了最高的CV。

### 标签编码/因式分解/内存减少
标签编码（分解）将（字符串、类别、对象）列转换为整数。类似get_dummies，不同点在于如果有几十个取值，如果用pd.get_dummies()则会得到好几十列，增加了数据的稀疏性

In [1]:
import numpy as np
import pandas as pd
df = pd.DataFrame(['green','bule','red','bule','green'],columns=['color'])
df['color'],_ = df['color'].factorize()
df

color
0      0
1      1
2      2
3      1
4      0

之后，可以将其转换为 int8、int16 或 int32用以减少内存，具体取决于 max 是否小于 128、小于 32768。

In [2]:
if df['color'].max()<128:
    df['color'] = df['color'].astype('int8')
elif df['color'].max()<32768:
    df['color'] = df['color'].astype('int16')
else: df['color'] = df['color'].astype('int32')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entries, 0 to 4
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype
---  ------  --------------  -----
 0   color   5 non-null      int8 
dtypes: int8(1)
memory usage: 133.0 bytes


In [3]:
df['color'] = df['color'].astype('int32')  # 如果使用int32，可以看到memory usage: 变成148了
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entries, 0 to 4
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype
---  ------  --------------  -----
 0   color   5 non-null      int32
dtypes: int32(1)
memory usage: 148.0 bytes


另外为了减少内存，人们memory_reduce在其他列上使用流行的功能。

一种更简单、更安全的方法是将所有 float64 转换为 float32，将所有 int64 转换为 int32。（最好避免使用 float16。如果你愿意，可以使用 int8 和 int16）。

In [4]:
for col in df.columns:
    if df[col].dtype=='float64': df[col] = df[col].astype('float32')
    if df[col].dtype=='int64': df[col] = df[col].astype('int32')

### 测试修改数据大小后，结果会不会发生变化

In [6]:
import numpy as np
import pandas as pd
import time

from sklearn.ensemble import RandomForestClassifier

from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import OrdinalEncoder

In [24]:
from sklearn.datasets import fetch_covtype
data = fetch_covtype()  # 森林植被类型
# 预处理
X, y = data['data'], data['target']
# 由于模型标签需要从0开始，所以数字需要全部减1
print('七分类任务，处理前：',np.unique(y))
print(y)
ord = OrdinalEncoder()
y = ord.fit_transform(y.reshape(-1, 1))
y = y.reshape(-1, )
print('七分类任务，处理后：',np.unique(y))
print(y)

X = pd.DataFrame(X,columns=data.feature_names)
X = X.iloc[:,:20]  # 数据集过大，这里仅用前20列做演示

y = pd.DataFrame(y, columns=data.target_names)

七分类任务，处理前： [1 2 3 4 5 6 7]
[5 5 2 ... 3 3 3]
七分类任务，处理后： [0. 1. 2. 3. 4. 5. 6.]
[4. 4. 1. ... 2. 2. 2.]


In [25]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 581012 entries, 0 to 581011
Data columns (total 20 columns):
 #   Column                              Non-Null Count   Dtype  
---  ------                              --------------   -----  
 0   Elevation                           581012 non-null  float64
 1   Aspect                              581012 non-null  float64
 2   Slope                               581012 non-null  float64
 3   Horizontal_Distance_To_Hydrology    581012 non-null  float64
 4   Vertical_Distance_To_Hydrology      581012 non-null  float64
 5   Horizontal_Distance_To_Roadways     581012 non-null  float64
 6   Hillshade_9am                       581012 non-null  float64
 7   Hillshade_Noon                      581012 non-null  float64
 8   Hillshade_3pm                       581012 non-null  float64
 9   Horizontal_Distance_To_Fire_Points  581012 non-null  float64
 10  Wilderness_Area_0                   581012 non-null  float64
 11  Wilderness_Area_1         

In [20]:
folds = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

In [21]:
%%time
val_acc_num=0
for fold_, (trn_idx, val_idx) in enumerate(folds.split(X, y)):
    print("第 {} 次训练...".format(fold_+1))
    train_x, trai_y = X.loc[trn_idx], y.loc[trn_idx]
    vali_x, vali_y = X.loc[val_idx], y.loc[val_idx]

    random_forest = RandomForestClassifier(n_estimators=1000,oob_score=True)
    random_forest.fit(train_x, trai_y.values.ravel())  # .values.ravel()是把DF格式变成1-D数组，上面出现的警告用这个解决

    # ===============验证集AUC操作===================
    pred_y = random_forest.predict(vali_x)
    print(accuracy_score(pred_y,vali_y.values.ravel()))
    val_acc_num += accuracy_score(pred_y,vali_y.values.ravel())
    
print("5折泛化，验证集ACC：{0:.7f}".format(val_acc_num/5))

第 1 次训练...
0.951731022434877
第 2 次训练...
0.952789514900648
第 3 次训练...
0.9518510869003975
第 4 次训练...
0.9518855097158396
第 5 次训练...
0.952023200977608
5折泛化，验证集AC：0.952
Wall time: 1h 48min 7s


上面输出的是3位尾数，5折加起来的均值为：0.952056

In [22]:
# 优化X内存使用率
for col in X.columns:
    if X[col].dtype=='float64': X[col] = X[col].astype('float32')
    if X[col].dtype=='int64': X[col] = [col].astype('int32')
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 581012 entries, 0 to 581011
Data columns (total 20 columns):
 #   Column                              Non-Null Count   Dtype  
---  ------                              --------------   -----  
 0   Elevation                           581012 non-null  float32
 1   Aspect                              581012 non-null  float32
 2   Slope                               581012 non-null  float32
 3   Horizontal_Distance_To_Hydrology    581012 non-null  float32
 4   Vertical_Distance_To_Hydrology      581012 non-null  float32
 5   Horizontal_Distance_To_Roadways     581012 non-null  float32
 6   Hillshade_9am                       581012 non-null  float32
 7   Hillshade_Noon                      581012 non-null  float32
 8   Hillshade_3pm                       581012 non-null  float32
 9   Horizontal_Distance_To_Fire_Points  581012 non-null  float32
 10  Wilderness_Area_0                   581012 non-null  float32
 11  Wilderness_Area_1         

In [23]:
%%time
val_acc_num=0
for fold_, (trn_idx, val_idx) in enumerate(folds.split(X, y)):
    print("第 {} 次训练...".format(fold_+1))
    train_x, trai_y = X.loc[trn_idx], y.loc[trn_idx]
    vali_x, vali_y = X.loc[val_idx], y.loc[val_idx]

    random_forest = RandomForestClassifier(n_estimators=1000,oob_score=True)
    random_forest.fit(train_x, trai_y.values.ravel())  # .values.ravel()是把DF格式变成1-D数组，上面出现的警告用这个解决

    # ===============验证集AUC操作===================
    pred_y = random_forest.predict(vali_x)
    print(accuracy_score(pred_y,vali_y.values.ravel()))
    val_acc_num += accuracy_score(pred_y,vali_y.values.ravel())
    
print("5折泛化，验证集ACC：{0:.7f}".format(val_acc_num/5))

第 1 次训练...
0.9512577127957109
第 2 次训练...
0.9529013880880872
第 3 次训练...
0.9521092580162132
第 4 次训练...
0.9516961842309083
第 5 次训练...
0.9520145952737474
5折泛化，验证集AC：0.952
Wall time: 1h 57min 11s


5折加起来的均值为：0.9519958，和上方的0.952056，仅差0.0000602，我测试了三轮，结果是接近一致的波动，由此证明减少内存是不影响结果的。

In [26]:
# 封装好的代码，原文链接：https://blog.csdn.net/wushaowu2014/article/details/86561141
def reduce_mem_usage(df):
    """ iterate through all the columns of a dataframe and modify the data type
        to reduce memory usage.        
    """
    start_mem = df.memory_usage().sum() / 1024**2
    print('Memory usage of dataframe is {:.2f} MB'.format(start_mem))
    
    for col in df.columns:
        col_type = df[col].dtype
        
        if col_type != object:
            c_min = df[col].min()
            c_max = df[col].max()
            if str(col_type)[:3] == 'int':
                if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
                    df[col] = df[col].astype(np.int16)
                elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
                    df[col] = df[col].astype(np.int64)  
            else:
                if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)
        else:
            df[col] = df[col].astype('category')
 
    end_mem = df.memory_usage().sum() / 1024**2
    print('Memory usage after optimization is: {:.2f} MB'.format(end_mem))
    print('Decreased by {:.1f}%'.format(100 * (start_mem - end_mem) / start_mem))
    
    return df

In [27]:
X = reduce_mem_usage(X)

Memory usage of dataframe is 88.66 MB
Memory usage after optimization is: 22.16 MB
Decreased by 75.0%


### 分类特征
对于分类变量，可以选择告诉 LGBM 它们是分类的（但内存会增加），或者可以告诉 LGBM 将其视为数字（首先需要对其进行标签编码）

In [17]:
df = pd.DataFrame(['green','bule','red','bule','green'],columns=['color'])
df['color'],_ = df['color'].factorize()
df['color'] = df['color'].astype('category')  # 转成分类特征并查看内存使用情况（已知int8内存使用是: 133.0 bytes）
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entries, 0 to 4
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype   
---  ------  --------------  -----   
 0   color   5 non-null      category
dtypes: category(1)
memory usage: 265.0 bytes


### Splitting
可以通过拆分将单个（字符串或数字）列分成两列。

例如，id_30诸如"Mac OS X 10_9_5"之类的字符串列可以拆分为操作系统"Mac OS X"和版本"10_9_5"。或者例如数字"1230.45"可以拆分为元" 1230"和分"45"。LGBM 无法单独看到这些片段，需要将它们拆分。

### 组合/转化/交互
两个（字符串或数字）列可以合并为一列。例如card1，card2可以成为一个新列

In [ ]:
df['uid'] = df['card1'].astype(str)+'_'+df['card2'].astype(str)

这有助于LGBM将card1和card2一起去与目标关联，并不会在树节点分裂他们。

但这种uid = card1_card2可能与目标相关，现在LGBM会将其拆分。数字列可以与加法、减法、乘法等组合使用。一个数字示例是

In [ ]:
df['x1_x2'] = df['x1'] * df['x2']

### 频率编码
频率编码是一种强大的技术，它允许 LGBM 查看列值是罕见的还是常见的。例如，如果您希望 LGBM“查看”哪些颜色不常使用，请尝试

In [19]:
temp = df['color'].value_counts().to_dict()
df['color_counts'] = df['color'].map(temp)
df

color  color_counts
0     0             2
1     1             2
2     2             1
3     1             2
4     0             2

### 聚合/组统计
为 LGBM 提供组统计数据允许 LGBM 确定某个值对于特定组是常见的还是罕见的。

可以通过为 pandas 提供 3 个变量来计算组统计数据。你给它组、感兴趣的变量和统计类型。例如

In [20]:
temp = df.groupby('color')['color_counts'].agg(['mean']).rename({'mean':'color_counts_mean'},axis=1)
df = pd.merge(df,temp,on='color',how='left')
df

color  color_counts  color_counts_sum
0     0             2                 4
1     1             2                 4
2     2             1                 1
3     1             2                 4
4     0             2                 4

此处的功能向每一行添加color_counts该行color组的平均值。因此，LGBM 现在可以判断color_counts对它们的color组是否为极少数的部分。

### 标准化
可以针对自己对列进行标准化。例如

In [22]:
df = pd.DataFrame(['green','bule','red','bule','green'],columns=['color'])
df['color'],_ = df['color'].factorize()
df['color'] = ( df['color']-df['color'].mean() ) / df['color'].std()
df

color
0 -0.956183
1  0.239046
2  1.434274
3  0.239046
4 -0.956183

或者你可以针对一列标准化另一列。例如，如果你创建一个组统计数据（如上所述）来指示D3每周的平均值。然后你可以通过

In [ ]:
df['D3_remove_time'] = df['D3'] - df['D3_week_mean']

D3_remove_time随着时间的推移，新变量不再增加，因为我们已经针对时间的影响对其进行了标准化。

### 离群值去除/平滑
通常，你希望从数据中删除异常，因为它们会混淆你的模型。然而，在风控等比赛中，我们想要发现异常，所以要谨慎使用平滑技术。

这些方法背后的想法是确定和删除不常见的值。例如，通过使用变量的频率编码，你可以删除所有出现小于 0.1% 的值，方法是将它们替换为 -9999 之类的新值（请注意，您应该使用与 NAN 使用的值不同的值）。